# Data exploration and preprocessing

In [1]:
# Import required libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from datasets import load_metric

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
from transformers import BertTokenizer, BertForMaskedLM, BertTokenizerFast

from transformers import pipeline
import torch
import re
import os

from masked_token_predictor_bert import MaskedTokenPredictorBert
from condbert import CondBertRewriter
from choosers import EmbeddingSimilarityChooser


Firstly, create and show image with half size in both axis with original ones.

In [2]:
df = pd.read_csv('filtered.tsv', sep='\t')
df = df.drop(['Unnamed: 0'], axis=1)

In [65]:
df.tail(5)
dataset = df.copy()
#dataset = dataset.head(200000)
dataset

reference  \
0       If Alkar is flooding her with psychic waste, t...   
1                               Now you're getting nasty.   
2                Well, we could spare your life, for one.   
3               Ah! Monkey, you've got to snap out of it.   
4                        I've got orders to put her down.   
...                                                   ...   
577772  You didn't know that Estelle had stolen some f...   
577773                    It'il suck the life out of you!   
577774                   I can't fuckin' take that, bruv.   
577775  They called me a fucking hero. The truth is I ...   
577776                               I did not screw him.   

                                              translation  similarity  \
0       if Alkar floods her with her mental waste, it ...    0.785171   
1                             you're becoming disgusting.    0.749687   
2                           well, we can spare your life.    0.919051   
3                            monkey, you have to wake up.    0.664333   
4                              I have orders to kill her.    0.726639   
...                                                   ...         ...   
577772  you didn't know that Estelle stole your fish f...    0.870322   
577773                  you'd be sucked out of your life!    0.722897   
577774                          I really can't take this.    0.617511   
577775         they said I was a hero, but I didn't care.    0.679613   
577776                                 I didn't fuck him.    0.868475   

        lenght_diff   ref_tox   trn_tox  
0          0.010309  0.014195  0.981983  
1          0.071429  0.065473  0.999039  
2          0.268293  0.213313  0.985068  
3          0.309524  0.053362  0.994215  
4          0.181818  0.009402  0.999348  
...             ...       ...       ...  
577772     0.030769  0.000121  0.949143  
577773     0.058824  0.996124  0.215794  
577774     0.212121  0.984538  0.000049  
577775     0.358209  0.991945  0.000124  
577776     0.095238  0.009480  0.994174  

[577777 rows x 6 columns]

In [66]:
aboba1 = np.mean(dataset["ref_tox"])
aboba2 = np.mean(dataset["trn_tox"])
print(aboba1, aboba2)

0.5413717990275281 0.4344898352213311


In [67]:
for i in dataset.index:
    if dataset.loc[i, 'trn_tox'] >= 0.5:
        print(i)
        # Swap 'reference' and 'translation'
        dataset.loc[i, 'reference'], dataset.loc[i, 'translation'] = dataset.loc[i, 'translation'], dataset.loc[i, 'reference']
        
        # Swap 'ref_tox' and 'trn_tox'
        dataset.loc[i, 'ref_tox'], dataset.loc[i, 'trn_tox'] = dataset.loc[i, 'trn_tox'], dataset.loc[i, 'ref_tox']

0
1
2
3
4
8
9
10
12
14
15
16
17
18
19
20
23
24
30
31
32
33
36
39
42
44
46
47
52
55
57
59
66
68
69
70
73
77
78
84
85
88
93
94
96
98
99
104
105
107
110
111
113
116
118
120
124
126
128
129
130
131
134
136
137
139
142
148
149
154
155
156
159
160
161
162
164
165
170
173
174
176
179
183
187
188
189
192
196
197
202
203
208
210
211
213
215
218
220
223
224
225
228
232
235
236
240
241
243
246
247
252
253
256
258
259
260
261
263
264
266
267
268
269
274
276
277
278
281
283
284
285
287
291
293
296
300
301
303
304
306
307
309
310
314
318
319
323
332
333
334
336
342
343
344
345
346
347
349
351
355
356
358
359
367
369
370
374
375
376
377
378
381
385
388
390
392
394
395
397
399
403
404
406
407
410
413
415
418
419
421
422
426
429
430
431
433
434
437
445
446
449
451
454
456
457
458
459
461
465
466
467
468
469
471
473
479
480
481
487
488
492
493
499
500
501
502
507
508
510
511
512
513
514
519
520
522
523
527
529
531
532
533
536
537
540
541
542
544
545
546
548
550
551
553
555
556
560
561
562
564
565
567
56

3969
3971
3972
3974
3976
3977
3978
3983
3986
3987
3988
3997
4002
4003
4004
4009
4012
4017
4018
4020
4022
4027
4028
4032
4034
4035
4044
4045
4046
4048
4049
4050
4055
4056
4058
4061
4066
4067
4069
4075
4076
4078
4079
4080
4084
4086
4087
4088
4094
4096
4097
4098
4099
4100
4102
4105
4107
4108
4110
4113
4114
4116
4117
4118
4120
4121
4124
4125
4130
4131
4132
4135
4138
4139
4140
4141
4143
4145
4149
4154
4157
4159
4161
4166
4171
4174
4176
4177
4178
4182
4183
4185
4186
4187
4191
4192
4195
4199
4201
4203
4204
4206
4210
4215
4216
4218
4220
4221
4223
4225
4226
4230
4233
4234
4235
4236
4238
4240
4242
4243
4245
4246
4247
4250
4252
4255
4256
4257
4258
4259
4260
4261
4267
4268
4270
4271
4273
4275
4281
4286
4288
4289
4290
4291
4294
4295
4296
4297
4298
4304
4308
4309
4311
4313
4314
4318
4319
4322
4327
4328
4330
4331
4334
4339
4340
4346
4351
4353
4356
4357
4359
4360
4362
4363
4364
4365
4366
4367
4368
4372
4374
4376
4378
4380
4381
4382
4384
4389
4390
4391
4392
4397
4398
4402
4403
4404
4405
4406
4408
4409


7601
7602
7607
7609
7610
7611
7613
7614
7615
7617
7618
7619
7620
7623
7624
7625
7629
7632
7633
7634
7635
7638
7639
7643
7644
7647
7650
7651
7652
7658
7659
7660
7661
7662
7663
7666
7667
7668
7669
7673
7676
7677
7678
7680
7683
7686
7687
7688
7689
7692
7694
7697
7701
7704
7705
7709
7710
7713
7714
7718
7720
7722
7723
7727
7728
7729
7731
7735
7736
7737
7738
7739
7740
7741
7742
7744
7748
7751
7752
7753
7754
7757
7758
7759
7763
7766
7768
7769
7770
7771
7772
7773
7775
7778
7780
7781
7783
7785
7788
7790
7791
7792
7793
7794
7795
7798
7799
7803
7807
7808
7812
7813
7814
7815
7816
7817
7818
7822
7824
7828
7829
7830
7832
7833
7834
7836
7840
7841
7844
7845
7849
7851
7852
7854
7856
7858
7859
7861
7863
7868
7872
7873
7875
7877
7879
7882
7883
7884
7887
7891
7894
7896
7897
7898
7899
7901
7902
7904
7905
7907
7908
7909
7910
7914
7918
7919
7921
7922
7923
7925
7926
7928
7930
7933
7935
7937
7938
7939
7940
7941
7942
7945
7947
7948
7951
7952
7953
7954
7958
7960
7961
7962
7963
7964
7965
7966
7967
7968
7969
7971


11081
11085
11086
11089
11091
11094
11097
11098
11099
11100
11105
11108
11109
11114
11119
11120
11123
11124
11126
11127
11133
11137
11138
11139
11140
11141
11142
11143
11144
11146
11147
11148
11149
11154
11159
11162
11165
11168
11174
11175
11179
11180
11185
11190
11191
11194
11196
11198
11199
11202
11203
11204
11212
11215
11216
11217
11218
11219
11223
11229
11230
11232
11233
11236
11237
11240
11247
11248
11251
11254
11255
11256
11259
11260
11261
11262
11265
11267
11268
11274
11275
11277
11280
11281
11282
11283
11289
11291
11294
11295
11296
11298
11299
11300
11302
11303
11304
11307
11309
11310
11311
11314
11316
11318
11320
11322
11323
11326
11327
11329
11330
11334
11337
11341
11342
11344
11348
11354
11362
11364
11365
11368
11371
11374
11376
11378
11382
11384
11385
11387
11392
11394
11395
11397
11399
11400
11401
11408
11410
11416
11417
11420
11421
11422
11423
11424
11425
11426
11427
11430
11431
11433
11435
11436
11438
11443
11450
11454
11456
11463
11465
11469
11470
11472
11475
11476
1147

14169
14170
14171
14172
14174
14178
14179
14184
14185
14192
14195
14198
14199
14201
14212
14213
14214
14218
14219
14223
14225
14226
14228
14231
14235
14237
14238
14239
14242
14245
14246
14248
14249
14252
14253
14263
14264
14267
14268
14271
14272
14273
14277
14281
14282
14286
14287
14289
14290
14294
14299
14301
14303
14310
14315
14316
14318
14323
14324
14328
14332
14335
14336
14338
14343
14348
14349
14350
14351
14352
14360
14361
14366
14367
14370
14371
14373
14374
14376
14377
14379
14382
14383
14384
14385
14387
14388
14392
14396
14398
14403
14404
14406
14408
14415
14419
14423
14425
14427
14428
14433
14434
14435
14438
14440
14441
14442
14444
14445
14448
14449
14450
14451
14452
14454
14455
14459
14464
14465
14467
14469
14473
14474
14477
14478
14479
14482
14485
14488
14489
14492
14494
14495
14500
14502
14505
14507
14508
14514
14518
14520
14522
14523
14524
14533
14534
14535
14537
14546
14551
14553
14554
14555
14559
14560
14563
14564
14565
14568
14569
14572
14575
14578
14579
14585
14586
1459

...

565161
565162
565163
565166
565169
565171
565172
565174
565177
565178
565180
565182
565183
565184
565185
565186
565187
565188
565189
565190
565192
565193
565196
565200
565203
565204
565206
565207
565208
565209
565212
565217
565221
565222
565223
565226
565231
565233
565234
565236
565237
565238
565239
565241
565243
565244
565246
565251
565253
565256
565257
565260
565262
565267
565268
565270
565272
565277
565279
565282
565284
565294
565295
565298
565303
565308
565309
565311
565313
565315
565316
565317
565318
565320
565325
565327
565328
565329
565334
565338
565340
565341
565342
565343
565345
565346
565347
565351
565353
565354
565355
565357
565359
565361
565367
565368
565369
565381
565382
565384
565385
565387
565389
565390
565391
565395
565397
565399
565400
565403
565409
565410
565415
565416
565420
565424
565426
565428
565431
565434
565436
565437
565438
565445
565450
565452
565454
565455
565457
565460
565461
565463
565464
565467
565470
565472
565475
565476
565478
565479
565482
565483
565493

567828
567830
567833
567834
567835
567842
567843
567845
567847
567848
567849
567850
567855
567858
567861
567863
567865
567874
567876
567877
567879
567881
567883
567889
567890
567892
567893
567898
567900
567906
567911
567912
567913
567914
567921
567922
567923
567925
567926
567928
567933
567934
567936
567937
567940
567941
567943
567945
567947
567948
567950
567954
567957
567958
567960
567966
567969
567971
567972
567976
567977
567981
567983
567984
567985
567987
567990
567991
567993
567994
567998
567999
568002
568003
568009
568010
568011
568012
568014
568016
568017
568019
568022
568023
568028
568031
568032
568034
568038
568039
568042
568043
568047
568049
568050
568051
568055
568056
568057
568059
568060
568063
568064
568065
568075
568077
568080
568085
568087
568089
568093
568094
568096
568098
568101
568104
568105
568107
568108
568111
568115
568117
568118
568119
568122
568123
568125
568127
568135
568136
568139
568140
568141
568142
568145
568147
568149
568151
568152
568153
568154
568159
568160

570471
570472
570474
570476
570479
570480
570482
570484
570488
570489
570490
570492
570496
570499
570501
570503
570504
570506
570510
570514
570516
570519
570520
570529
570530
570533
570534
570535
570536
570541
570542
570546
570547
570548
570549
570550
570552
570555
570558
570564
570565
570567
570573
570574
570575
570578
570579
570581
570582
570583
570584
570586
570588
570590
570598
570600
570604
570606
570607
570611
570613
570615
570617
570622
570624
570625
570628
570630
570631
570634
570636
570641
570645
570646
570647
570649
570653
570655
570658
570660
570663
570665
570667
570670
570671
570674
570679
570680
570681
570682
570683
570684
570686
570687
570690
570692
570696
570700
570701
570703
570704
570706
570707
570709
570712
570713
570715
570718
570719
570720
570721
570723
570724
570726
570727
570736
570737
570739
570742
570745
570748
570749
570753
570756
570757
570759
570760
570765
570768
570771
570772
570773
570776
570777
570778
570780
570783
570792
570793
570794
570795
570796
570798

573053
573058
573060
573062
573063
573064
573070
573071
573073
573077
573078
573081
573084
573086
573091
573093
573095
573096
573098
573099
573102
573107
573108
573110
573111
573112
573115
573116
573121
573122
573123
573124
573125
573128
573129
573132
573134
573136
573138
573139
573141
573143
573144
573151
573152
573153
573154
573155
573156
573157
573158
573164
573166
573167
573171
573174
573176
573177
573178
573179
573182
573183
573188
573189
573192
573196
573199
573200
573201
573203
573204
573207
573208
573211
573212
573215
573217
573219
573220
573222
573226
573228
573230
573231
573235
573241
573244
573246
573247
573251
573252
573253
573254
573256
573257
573260
573262
573264
573265
573267
573270
573271
573272
573274
573278
573279
573281
573282
573283
573285
573286
573289
573292
573293
573294
573297
573300
573301
573303
573305
573308
573310
573311
573313
573321
573322
573323
573324
573325
573327
573328
573330
573333
573337
573339
573340
573341
573345
573346
573347
573348
573356
573358

575649
575651
575652
575660
575661
575662
575664
575665
575666
575667
575670
575671
575672
575678
575679
575683
575684
575685
575686
575687
575688
575694
575695
575696
575697
575700
575703
575704
575705
575709
575714
575715
575716
575717
575721
575723
575725
575728
575733
575734
575737
575738
575740
575741
575742
575744
575747
575749
575751
575753
575754
575755
575756
575757
575758
575759
575761
575763
575768
575772
575774
575775
575776
575779
575781
575782
575784
575788
575789
575790
575793
575794
575795
575798
575803
575807
575813
575814
575817
575819
575820
575823
575826
575827
575829
575830
575833
575835
575838
575840
575842
575844
575845
575846
575850
575851
575852
575858
575859
575860
575862
575864
575865
575868
575871
575872
575876
575878
575881
575883
575884
575885
575886
575889
575890
575891
575892
575895
575896
575897
575900
575908
575912
575919
575925
575928
575936
575938
575939
575942
575943
575946
575948
575949
575950
575951
575952
575954
575958
575960
575964
575966
575969

In [68]:
dataset.to_csv('dataset.csv', index=False)

In [70]:
dataset = pd.read_csv('dataset.csv')
dataset

reference  \
0       if Alkar floods her with her mental waste, it ...   
1                             you're becoming disgusting.   
2                           well, we can spare your life.   
3                            monkey, you have to wake up.   
4                              I have orders to kill her.   
...                                                   ...   
577772  you didn't know that Estelle stole your fish f...   
577773                    It'il suck the life out of you!   
577774                   I can't fuckin' take that, bruv.   
577775  They called me a fucking hero. The truth is I ...   
577776                                 I didn't fuck him.   

                                              translation  similarity  \
0       If Alkar is flooding her with psychic waste, t...    0.785171   
1                               Now you're getting nasty.    0.749687   
2                Well, we could spare your life, for one.    0.919051   
3               Ah! Monkey, you've got to snap out of it.    0.664333   
4                        I've got orders to put her down.    0.726639   
...                                                   ...         ...   
577772  You didn't know that Estelle had stolen some f...    0.870322   
577773                  you'd be sucked out of your life!    0.722897   
577774                          I really can't take this.    0.617511   
577775         they said I was a hero, but I didn't care.    0.679613   
577776                               I did not screw him.    0.868475   

        lenght_diff   ref_tox   trn_tox  
0          0.010309  0.981983  0.014195  
1          0.071429  0.999039  0.065473  
2          0.268293  0.985068  0.213313  
3          0.309524  0.994215  0.053362  
4          0.181818  0.999348  0.009402  
...             ...       ...       ...  
577772     0.030769  0.949143  0.000121  
577773     0.058824  0.996124  0.215794  
577774     0.212121  0.984538  0.000049  
577775     0.358209  0.991945  0.000124  
577776     0.095238  0.994174  0.009480  

[577777 rows x 6 columns]

In [7]:
aboba1 = np.mean(dataset["ref_tox"])
aboba2 = np.mean(dataset["trn_tox"])
print(aboba1, aboba2)

0.9400417279332877 0.036612862385495604


In [49]:
texts[:5]

['If Alkar is flooding her with psychic waste, that explains the high level of neurotransmitters.',
 "Now you're getting nasty.",
 'Well, we could spare your life, for one.',
 "Ah! Monkey, you've got to snap out of it.",
 "I've got orders to put her down."]

In [32]:
texts = df["reference"].iloc[:10000].tolist()
labels = (df["ref_tox"].iloc[:10000] >= 0.5).astype(int).tolist()
toxic_sentence = []
nontoxic_sentence = []

for i in range(10000):
    if labels[i] == 0:
        nontoxic_sentence.append(texts[i])
    else:
        toxic_sentence.append(texts[i])

In [48]:
toxic_sentence = list(dataset['reference'][:50000])
nontoxic_sentence = list(dataset['translation'][:50000])
toxic_labels = [1 for i in range(len(toxic_sentence))]
nontoxic_labels = [0 for i in range(len(nontoxic_sentence))]

In [50]:
print(toxic_sentence[20:30])
nontoxic_sentence[20:30]

['the foolish Xerxes calmly passed all control of the computer network and commanded her to handle any kind of trouble.', "That night, Li'l Dice satisfied his thirst to kill, though he knew Shaggy would never forgive him.", 'Real life starts the first time you fuck, kid.', "I think you're the weirdest person I've ever met.", "I mean, I think it's fucking crazy I'm talking to you.", "Shit, this one I can't even pronounce.", 'I like that shit.', "Trying to keep me fucking drugged so I don't know what's going on.", 'How is this not porn? This is porn that comes home.', 'Hey, leave the poor bastard alone!']


['Fatuous Xerxes blithely surrendered control to the computer grid, ordering it to take care of whatever troubles might arise.',
 'that night, he satisfied his blood lust, and knew Hairy would never forgive him.',
 'boy, real life starts up first.',
 "I think you are the strangest man I've ever met.",
 "I say creepy, I mean, it's totally batshit crazy I can even talk to you.",
 "gosh, I can't even pronounce this.",
 'I love it.',
 "you want to fool me so I don't know what's going on.",
 "and this doesn't feel like porn?",
 'leave the poor man alone!']

In [53]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
from scipy.sparse import vstack

# Load pre-trained model and tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertForMaskedLM.from_pretrained('bert-base-uncased')

# Initialize the CountVectorizer with a limited number of features
vectorizer = CountVectorizer(max_features=30000)

# Vectorize the toxic and non-toxic sentences separately to save memory
X_toxic = vectorizer.fit_transform(toxic_sentence)
X_nontoxic = vectorizer.transform(nontoxic_sentence)

# Stack the vectorized sentences
X = vstack([X_toxic, X_nontoxic])

# Prepare the labels
labels = toxic_labels + nontoxic_labels

# Train the logistic regression model
lr_model = LogisticRegression()
lr_model.fit(X, labels)

# Get the feature names (words) and their weights from the logistic regression model
feature_names = vectorizer.get_feature_names_out()
feature_weights = lr_model.coef_[0]

# Create a dictionary mapping words to their toxicity scores (weights)
word_toxicity_scores = dict(zip(feature_names, feature_weights))

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'bert.pooler.dense.weight', 'bert.pooler.dense.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
C:\Users\markz\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\linear_model\_logistic.py:444: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-lea

In [54]:
len(word_toxicity_scores)

23502

In [55]:
# Initialize lists to store toxic and non-toxic words
toxic_words_in_sentences = []
non_toxic_words_in_sentences = []

for i in range(len(toxic_sentence + nontoxic_sentence)):
    # Split the sentence into words, considering punctuation
    words = re.findall(r'\b\w+\b', (toxic_sentence + nontoxic_sentence)[i])
    
    # Compute the toxicity scores for the words
    scores = [word_toxicity_scores.get(word, 0) for word in words]
    
    # Compute the threshold
    t1 = max(0.2, max(scores)/2)

    # Increase the threshold for non-toxic words
    t2 = 0

    # Find the toxic and non-toxic words
    toxic_words = [word for word, score in zip(words, scores) if score > t1]
    non_toxic_words = [word for word, score in zip(words, scores) if score <= t2]
    
    toxic_words_in_sentences.append(toxic_words)
    non_toxic_words_in_sentences.append(non_toxic_words)

# Flatten the lists of lists into single lists
toxic_words_in_sentences = [item for sublist in toxic_words_in_sentences for item in sublist]
non_toxic_words_in_sentences = [item for sublist in non_toxic_words_in_sentences for item in sublist]

In [60]:
toxic_words_in_sentences = list(set(toxic_words_in_sentences))
non_toxic_words_in_sentences = list(set(non_toxic_words_in_sentences))

In [62]:
len(toxic_words_in_sentences)

3722

In [42]:
tokenized_sentences = [tokenizer.tokenize(sentence) for sentence in (toxic_sentence + nontoxic_sentence)]
token_weights = [[word_toxicity_scores.get(token, 0) for token in sentence] for sentence in tokenized_sentences]

token_toxicities = []
for token in tokenizer.get_vocab():
    weights = [weight for sentence, weights in zip(tokenized_sentences, token_weights) if token in sentence for weight in weights]
    if weights:
        toxicity = np.mean(weights)
    else:
        toxicity = 0  # default toxicity for tokens that don't appear in the sentences
    token_toxicities.append(toxicity)
    
token_toxicities[0]

KeyboardInterrupt: 

In [42]:
token_toxicities = []
for token in tokenizer.get_vocab():
    words_with_token = [word for word in feature_names if token in word]
    if words_with_token:
        toxicity = np.mean([word_toxicity_scores[word] for word in words_with_token])
    else:
        toxicity = 0  # default toxicity for tokens that don't appear in the words
    token_toxicities.append(toxicity)
    
token_toxicities[1000:1100]

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.03861492692139938,
 0.02383089697304741,
 -0.029741304685376464,
 0.0855282876835952,
 -0.03506117288034508,
 -0.09465797327572653,
 -0.027512827025949968,
 -0.0585955217424324,
 -0.05023428354590029,
 0.15349023049093097,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.056873393676680206,
 0,
 0.011884248936145756,
 0.01370186408729019,
 0.023342791241472195,
 0.004757029797333329,
 -0.002902137147259999,
 0.03248370619667477,
 0.011041683694920994,
 0.018977855004638645,
 0.018864313696498734,
 -0.005647144197924392,
 0.0595641939153494,
 0.005660097295253665,
 0.00621307683014543,
 0.004183370516917806,
 -0.005682475714536461,
 -0.00912356672798723,
 -0.01852143789766503,
 0.010389946705308736,
 0.0172049741987804,
 0.014534753974565344,
 0.024666181440807986,
 -0.002211416096191966,
 -0.009763826751953407,
 -0.009250799007234961,
 -0.009355962316119387,
 0.0065519101331000685,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [43]:
bimba = texts[20:30]

In [63]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')
masked_model = BertForMaskedLM.from_pretrained('bert-base-uncased')

def adjust_logits(logits, label=0):
    return logits - token_toxicities * 100 * (1 - 2 * label)

predictor = MaskedTokenPredictorBert(masked_model, tokenizer, max_len=250, device=device, label=0,
                                     contrast_penalty=0.0, logits_postprocessor=adjust_logits)

editor = CondBertRewriter(
    model=masked_model,
    tokenizer=tokenizer,
    device=device,
    neg_words=toxic_words_in_sentences,
    pos_words=non_toxic_words_in_sentences,
    word2coef=word_toxicity_scores,
    token_toxicities=np.array(token_toxicities),
    predictor=predictor,
)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'bert.pooler.dense.weight', 'bert.pooler.dense.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [64]:
bimba = toxic_sentence[20:30]
for sentence in bimba:
    print(sentence)
    print(editor.translate(sentence, prnt=False))

the foolish Xerxes calmly passed all control of the computer network and commanded her to handle any kind of trouble.
the foolish xerxes calmly passed all control of the computer network and commanded her to handle any kind of trouble.
That night, Li'l Dice satisfied his thirst to kill, though he knew Shaggy would never forgive him.
that night, li ' l dice satisfied his thirst to kill, though he knew shaggy would never forgive him.
Real life starts the first time you fuck, kid.
real life starts the first time you fuck, kid.
I think you're the weirdest person I've ever met.
i think you ' re the weirdst person i ' ve ever met.
I mean, I think it's fucking crazy I'm talking to you.
i mean, i think it ' s fucking crazy i ' m talking to you.
Shit, this one I can't even pronounce.
., this one i can ' t even pronounce.
I like that shit.
i like that stuff.
Trying to keep me fucking drugged so I don't know what's going on.
trying to keep me fucking drugged so i don ' t know what ' s going on.
H

In [47]:
metric = load_metric("sacrebleu")

C:\Users\markz\AppData\Local\Temp\ipykernel_13660\2163898601.py:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("sacrebleu")


In [61]:
bimba1 = list(dataset['reference'][0:10])
bimba2 = list(dataset['translation'][0:10])
bimba_pred = []
bimba1

['if Alkar floods her with her mental waste, it would explain the high levels of neurotransmitter.',
 "you're becoming disgusting.",
 'well, we can spare your life.',
 'monkey, you have to wake up.',
 'I have orders to kill her.',
 "I'm not gonna have a child... ...with the same genetic disorder as me who's gonna die. L...",
 "They're all laughing at us, so we'll kick your ass.",
 'Maine was very short on black people back then.',
 'Briggs, what the hell is going on?',
 "another simply didn't know what to do, so whenever he met my brother, he nearly beat the shit out of him."]

In [71]:
bimba2 = [[sen] for sen in bimba2]
bimba2

[['If Alkar is flooding her with psychic waste, that explains the high level of neurotransmitters.'],
 ["Now you're getting nasty."],
 ['Well, we could spare your life, for one.'],
 ["Ah! Monkey, you've got to snap out of it."],
 ["I've got orders to put her down."],
 ["I'm not going to breed kids with a genetic disorder that makes them die."],
 ["they're laughing at us. We'll show you."],
 ["there wasn't much black in Maine then."],
 ["Briggs, what the hell's happening?"],
 ["Another one simply had no clue what to do, so whenever he met my brother he'd beat the crap out of him, and then say:"]]

In [63]:
for sentence in bimba1:
    bimba_pred.append((editor.translate(sentence, prnt=False)))

['If Alkar is flooding her with psychic waste, that explains the high level of neurotransmitters.',
 "Now you're getting nasty.",
 'Well, we could spare your life, for one.',
 "Ah! Monkey, you've got to snap out of it.",
 "I've got orders to put her down.",
 "I'm not going to breed kids with a genetic disorder that makes them die.",
 "they're laughing at us. We'll show you.",
 "there wasn't much black in Maine then.",
 "Briggs, what the hell's happening?",
 "Another one simply had no clue what to do, so whenever he met my brother he'd beat the crap out of him, and then say:"]

In [72]:
metric.compute(predictions=bimba_pred, references=bimba2)

{'score': 10.655955129144063,
 'counts': [51, 21, 7, 4],
 'totals': [139, 129, 119, 109],
 'precisions': [36.69064748201439,
  16.27906976744186,
  5.882352941176471,
  3.669724770642202],
 'bp': 1.0,
 'sys_len': 139,
 'ref_len': 120}

In [ ]:
# Load pre-trained model and tokenizer
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')
masked_model = BertForMaskedLM.from_pretrained('bert-base-uncased')

for sentence in bimba:
    # Tokenize the sentence
    inputs = tokenizer(sentence, return_tensors='pt', truncation=True, padding=True)

    # Identify the toxic words and replace them with [MASK]
    input_ids = inputs['input_ids'].tolist()[0]
    for i in range(len(input_ids)):
        if tokenizer.decode([input_ids[i]]) in toxic_words_in_sentences:
            input_ids[i] = tokenizer.mask_token_id

    # Convert back to tensors
    inputs['input_ids'] = torch.tensor([input_ids])

    # Predict the masked tokens
    outputs = model(**inputs)
    predictions = outputs.logits

    # Get the predicted tokens
    predicted_ids = torch.argmax(predictions, dim=2)

    # Decode the tokens to strings
    predicted_sentence = tokenizer.decode(predicted_ids[0])

    print(predicted_sentence)



# Load pre-trained model and tokenizer
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')
masked_model = BertForMaskedLM.from_pretrained('bert-base-uncased')

# For each sentence
for i in range(len(bimba)):
    # Tokenize the sentence into words and punctuation
    tokens = re.findall(r"\b\w+\b|[\.,!?']", bimba[i])
    
    # Replace toxic words with [MASK]
    for j in range(len(tokens)):
        if tokens[j] in toxic_words_in_sentences:
            tokens[j] = '[MASK]'
    
    # Join the tokens back into a sentence
    bimba[i] = ' '.join(tokens)
    
    print(bimba[i])


bimba = texts[20:30]

# Load pre-trained model and tokenizer
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')
masked_model = BertForMaskedLM.from_pretrained('bert-base-uncased')

# Create a dictionary mapping tokens to their toxicity scores
token_toxicities = {tokenizer.encode(word, add_special_tokens=False)[0]: 1 for word in toxic_words_in_sentences}


# For each sentence in 'bimba'
for i in range(len(bimba)):
    # Tokenize the sentence into words and punctuation
    tokens = re.findall(r"\b\w+\b|[\.,!?']", bimba[i])
    
    # Identify toxic words
    toxic_word_indices = [j for j in range(len(tokens)) if tokens[j] in toxic_words_in_sentences]
    
    # Replace toxic words with [MASK] and preserve original tokens
    original_tokens = tokens.copy()
    for j in toxic_word_indices:
        tokens[j] = '[MASK]'
    
    # Join the tokens back into a sentence
    bimba[i] = ' '.join(tokens)
    
    print(bimba[i])